<a href="https://colab.research.google.com/github/lutakrystal305/DL_basic/blob/main/CaptionImage.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
from google.colab import drive
drive.mount('/content/gdrive/')

Mounted at /content/gdrive/


In [1]:
!mkdir Flickr8k

In [3]:
%cd Flickr8k
!unzip /content/gdrive/MyDrive/Flick8r/Flickr8k_Dataset.zip


taset/3726025663_e7d35d23f6.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726025663_e7d35d23f6.jpg  
  inflating: Flicker8k_Dataset/3726076549_0efb38854b.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726076549_0efb38854b.jpg  
  inflating: Flicker8k_Dataset/3726120436_740bda8416.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726120436_740bda8416.jpg  
  inflating: Flicker8k_Dataset/3726130458_07df79e969.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726130458_07df79e969.jpg  
  inflating: Flicker8k_Dataset/3726168984_1fa2c8965b.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726168984_1fa2c8965b.jpg  
  inflating: Flicker8k_Dataset/3726170067_094cc1b7e5.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726170067_094cc1b7e5.jpg  
  inflating: Flicker8k_Dataset/3726590391_bc6e729bb6.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726590391_bc6e729bb6.jpg  
  inflating: Flicker8k_Dataset/3726629271_7639634703.jpg  
  inflating: __MACOSX/Flicker8k_Dataset/._3726629271_7639634703

In [4]:
!mkdir Flickr8k_text
%cd /content/Flickr8k/Flickr8k_text
!unzip /content/gdrive/MyDrive/Flick8r/Flickr8k_text.zip

/content/Flickr8k/Flickr8k_text
Archive:  /content/gdrive/MyDrive/Flick8r/Flickr8k_text.zip
  inflating: CrowdFlowerAnnotations.txt  
  inflating: ExpertAnnotations.txt   
  inflating: Flickr8k.lemma.token.txt  
   creating: __MACOSX/
  inflating: __MACOSX/._Flickr8k.lemma.token.txt  
  inflating: Flickr8k.token.txt      
  inflating: Flickr_8k.devImages.txt  
  inflating: Flickr_8k.testImages.txt  
  inflating: Flickr_8k.trainImages.txt  
  inflating: readme.txt              


In [5]:
%cd /content

/content


In [6]:
!pwd

/content


In [7]:
!unzip /content/gdrive/MyDrive/glove.6B.zip


Archive:  /content/gdrive/MyDrive/glove.6B.zip
  inflating: glove.6B.100d.txt       
  inflating: glove.6B.200d.txt       
  inflating: glove.6B.300d.txt       
  inflating: glove.6B.50d.txt        


In [9]:
import numpy as np
from numpy import array
import pandas as pd
import matplotlib.pyplot as plt
import string
import os
from PIL import Image
import glob
from pickle import dump, load
from time import time
from keras.preprocessing import sequence
from keras.models import Sequential
from keras.layers import LSTM, Embedding, TimeDistributed, Dense, RepeatVector, Activation, Flatten, Reshape, concatenate, Dropout, BatchNormalization
from keras.optimizers import Adam, RMSprop
from keras.layers.wrappers import Bidirectional
from keras.layers.merge import add
from keras.applications.inception_v3 import InceptionV3
from keras.preprocessing import image
from keras.models import Model
from keras import Input, layers
from keras import optimizers
from keras.applications.inception_v3 import preprocess_input
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils.np_utils import to_categorical

In [11]:
path_to_desc = '/content/Flickr8k/Flickr8k_text/Flickr8k.token.txt'
def load_doc(filename):
  file = open(filename, 'r')
  text = file.read()
  file.close()
  return text
doc = load_doc(path_to_desc)
print(doc)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [15]:
def load_description(doc):
  mapping = dict()
  for line in doc.split('\n'):
    tokens = line.split() #-> [id.jpg, word1, word2, ...]
    #print(tokens)
    if len(line) < 2:
      continue
    image_id, image_desc = tokens[0], tokens[1:]
    image_id = image_id.split('.')[0]
    image_desc = ' '.join(image_desc)
    #print(image_desc)
    if image_id not in mapping:
      mapping[image_id] = list()
    mapping[image_id].append(image_desc)
  return mapping
descriptions = load_description(doc) # -> [id: [sequences]]
print(descriptions)

{'1000268201_693b08cb0e': ['A child in a pink dress is climbing up a set of stairs in an entry way .', 'A girl going into a wooden building .', 'A little girl climbing into a wooden playhouse .', 'A little girl climbing the stairs to her playhouse .', 'A little girl in a pink dress going into a wooden cabin .'], '1001773457_577c3a7d70': ['A black dog and a spotted dog are fighting', 'A black dog and a tri-colored dog playing with each other on the road .', 'A black dog and a white dog with brown spots are staring at each other in the street .', 'Two dogs of different breeds looking at each other on the road .', 'Two dogs on pavement moving toward each other .'], '1002674143_1b742ab4b8': ['A little girl covered in paint sits in front of a painted rainbow with her hands in a bowl .', 'A little girl is sitting in front of a large painted rainbow .', 'A small girl in the grass plays with fingerpaints in front of a white canvas with a rainbow on it .', 'There is a girl with pigtails sitting

In [38]:
def clean_description(descriptions):
  table = str.maketrans('', '', string.punctuation)
  for key, desc_list in descriptions.items():
    print(key, desc_list)
    for i in range(len(desc_list)):
      desc = desc_list[i]
      desc = desc.split()
      desc = [word.lower() for word in desc]
      desc = [w.translate(table) for w in desc]
      print(desc)
      desc = [word for word in desc if len(word) > 1]
      desc = [word for word in desc if word.isalpha()]
      desc_list[i] = ' '.join(desc)
      print(desc_list[i])

clean_description(descriptions)
#xu li cau (chu thuong, bo so, ...)


Kết quả truyền trực tuyến bị cắt bớt đến 5000 dòng cuối.
['woman', 'works', 'hard', 'to', 'maintain', 'fingerhold', 'as', 'she', 'climbs', 'rock', 'face']
woman works hard to maintain fingerhold as she climbs rock face
['man', 'straining', 'to', 'climb', 'cliff', 'face']
man straining to climb cliff face
['the', 'gal', 'in', 'the', 'yellow', 'hardhat', 'is', 'rock', 'climbing', 'up', 'the', 'steep', 'rock']
the gal in the yellow hardhat is rock climbing up the steep rock
527946505_a51ade1578 ['black dog about to jump into lack to get small ball', 'black dog gets ready to jump into the water', 'black dog is preparing to jump off dock into the water to fetch ball', 'black dog on dock about to dive into the water after ball', 'dog leans off the dock to fetch ball in the water']
['black', 'dog', 'about', 'to', 'jump', 'into', 'lack', 'to', 'get', 'small', 'ball']
black dog about to jump into lack to get small ball
['black', 'dog', 'gets', 'ready', 'to', 'jump', 'into', 'the', 'water']
blac

In [42]:
def save_description(descriptions, filename):
  lines = list();
  for key, desc_list in descriptions.items():
    for desc in desc_list:
      lines.append(key + ' ' + desc)
    
  data = '\n'.join(lines)
  file = open(filename, 'w')
  file.write(data)
  file.close()
#lưu từng dòng "id sequence" vào (nếu id có nhiều sequence thì sẽ nhiều dòng như vậy)
save_description(descriptions, 'descriptions.txt')

In [43]:
################################ II. PHẦN ĐỌC ẢNH  ẢNH ############################
path_to_train_id_file = 'Flickr8k/Flickr8k_text/Flickr_8k.trainImages.txt'
path_to_test_id_file ='Flickr8k/Flickr8k_text/Flickr_8k.testImages.txt'
path_to_image_folder = 'Flickr8k/Flicker8k_Dataset/'


In [44]:
#lay id ảnh của tập train
def load_set(filename):
  doc = load_doc(filename)
  dataset = list()
  for line in doc.split('\n'):
    if len(line) < 1:
      continue
    identify = line.split('.')[0]
    dataset.append(identify)
  return set(dataset)

train_id = load_set(path_to_train_id_file)
print(train_id)


Kết quả truyền trực tuyến bị cắt bớt đến 5000 dòng cuối.
3487261028_30791528ec
3136043366_b3f8607a0e
3475005101_6f6e437459
3472270112_0a7cb7b27c
2868668723_0741222b23
3500342526_393c739e2f
542405691_0594b1ce72
421153376_d1d325568f
430964917_022995afb6
1597319381_1e80d9e39c
405331006_4e94e07698
3493000349_81c540e828
505955292_026f1489f2
3122497129_d08f5729b8
3428386573_670f5362f0
2269961438_cae7a9c725
3156113206_53c2a7b5d8
3725177385_62d5e13634
3590654365_fd4819f48b
3178371973_60c6b8f110
1402641725_5e027ecaa7
1449625950_fc9a8d02d9
2836808985_b26e4ca09e
506412121_67ecc7ec05
944788251_a0bcd4b960
2714878018_1593c38d69
3050606344_af711c726c
2488795251_c108c77b13
2613920405_e91e6ebd7a
109823397_e35154645f
2470519275_65725fd38d
1341787777_4f1ebb1793
2907244809_07ab2c6b6c
2562377955_8d670ccec6
3510218982_318f738b76
1287064529_aa4e4f3c31
3372022051_132b8e6233
2804374083_311f98f5f2
408627152_1feaa4b94e
3653837067_94050699ec
1517340899_ee1c74a8f6
3708743823_3e3e0554d1
3569755200_cef7ee2233
547238

In [45]:
#Lấy các ảnh jpg chứa trong thư mục toàn bộ ảnh flickr
all_train_images_in_folder = glob.glob(path_to_image_folder + '*.jpg')
# Đọc toàn bộ nội dung file danh sách các file ảnh dùng để train
train_images = set(open(path_to_train_id_file, 'r').read().strip().split('\n'))
print(train_images)
# Danh sách ấy sẽ lưu full path vào biến train_img
train_img = []
for img in all_train_images_in_folder:
  if img[len(path_to_image_folder):] in train_images:
    train_img.append(img)
print(train_img)

Kết quả truyền trực tuyến bị cắt bớt đến 5000 dòng cuối.
Flickr8k/Flicker8k_Dataset/3250076419_eb3de15063.jpg
Flickr8k/Flicker8k_Dataset/143237785_93f81b3201.jpg
Flickr8k/Flicker8k_Dataset/3534824784_7133119316.jpg
Flickr8k/Flicker8k_Dataset/3111897772_5211a37a02.jpg
Flickr8k/Flicker8k_Dataset/3576536763_3c8c4f232e.jpg
Flickr8k/Flicker8k_Dataset/762947607_2001ee4c72.jpg
Flickr8k/Flicker8k_Dataset/3445544288_68fdb25969.jpg
Flickr8k/Flicker8k_Dataset/3488087117_2719647989.jpg
Flickr8k/Flicker8k_Dataset/3328397409_092de2bd32.jpg
Flickr8k/Flicker8k_Dataset/3396043950_12783c5147.jpg
Flickr8k/Flicker8k_Dataset/2339573065_91f1e3be60.jpg
Flickr8k/Flicker8k_Dataset/2800934095_b84a5009dd.jpg
Flickr8k/Flicker8k_Dataset/3737711435_113ccd0a52.jpg
Flickr8k/Flicker8k_Dataset/487894806_352d9b5e66.jpg
Flickr8k/Flicker8k_Dataset/3228793611_8f260ea500.jpg
Flickr8k/Flicker8k_Dataset/3243591844_791cfa62eb.jpg
Flickr8k/Flicker8k_Dataset/3530504007_3272c57e21.jpg
Flickr8k/Flicker8k_Dataset/3376972502_35e3e11

In [47]:
# 2. -------- Xử lý ảnh dùng để test (xử lý tương tự) -------------------------------------

test_images = set(open(path_to_train_id_file, 'r').read().strip().split('\n'))
test_img = []

for img in all_train_images_in_folder:
    if img[len(path_to_image_folder):] in test_images:
        test_img.append(img)

In [54]:
############################ III. PHẦN XỬ LÝ DỮ LIỆU MÔ TẢ ############################
def load_clean_description(filename, dataset):
  doc = load_doc(filename)
  descriptions = dict()
  for line in doc.split('\n'):
    tokens = line.split() #-> [id, word1, word2, ...]
    image_id, image_desc = tokens[0], tokens[1:]
    if image_id in dataset:
      if image_id not in descriptions:
        descriptions[image_id] = list()
      desc = 'startseq ' + ' '.join(image_desc) + ' endseq' #them "startseq" va "endseq"
      descriptions[image_id].append(desc)
  return descriptions
train_descriptions = load_clean_description('descriptions.txt', train_id)
print(train_descriptions) #-> [id: ['startseq'+seq1+'endseq', 'startseq' + seq2 + 'endseq', ...]]

{'1000268201_693b08cb0e': ['startseq child in pink dress is climbing up set of stairs in an entry way endseq', 'startseq girl going into wooden building endseq', 'startseq little girl climbing into wooden playhouse endseq', 'startseq little girl climbing the stairs to her playhouse endseq', 'startseq little girl in pink dress going into wooden cabin endseq'], '1001773457_577c3a7d70': ['startseq black dog and spotted dog are fighting endseq', 'startseq black dog and tricolored dog playing with each other on the road endseq', 'startseq black dog and white dog with brown spots are staring at each other in the street endseq', 'startseq two dogs of different breeds looking at each other on the road endseq', 'startseq two dogs on pavement moving toward each other endseq'], '1002674143_1b742ab4b8': ['startseq little girl covered in paint sits in front of painted rainbow with her hands in bowl endseq', 'startseq little girl is sitting in front of large painted rainbow endseq', 'startseq small 

In [55]:
all_train_caption = []
for key, val  in train_descriptions.items():
  for cap in val: #lấy ra từng caption trong value (nhiều caption)
    all_train_caption.append(cap)
len(all_train_caption)

30000

In [56]:
#Chỉ lấy những từ được lặp lại trên 10 lần
word_count_thresold = 10
word_count = {}
nsents = 0
for sent in all_train_caption:
  nsents += 1
  for w in sent.split(' '):
    word_count[w] = word_count.get(w, 0) + 1

vocab = [w for w in word_count if word_count[w] >= word_count_thresold]
print(vocab)

['startseq', 'child', 'in', 'pink', 'dress', 'is', 'climbing', 'up', 'set', 'of', 'stairs', 'an', 'way', 'endseq', 'girl', 'going', 'into', 'wooden', 'building', 'little', 'the', 'to', 'her', 'black', 'dog', 'and', 'spotted', 'are', 'fighting', 'tricolored', 'playing', 'with', 'each', 'other', 'on', 'road', 'white', 'brown', 'spots', 'staring', 'at', 'street', 'two', 'dogs', 'different', 'looking', 'pavement', 'moving', 'toward', 'covered', 'paint', 'sits', 'front', 'painted', 'rainbow', 'hands', 'bowl', 'sitting', 'large', 'small', 'grass', 'plays', 'it', 'there', 'pigtails', 'painting', 'young', 'outside', 'man', 'lays', 'bench', 'while', 'his', 'by', 'him', 'which', 'also', 'tied', 'sleeping', 'next', 'shirtless', 'lies', 'park', 'laying', 'holding', 'leash', 'ground', 'orange', 'hat', 'something', 'wears', 'glasses', 'wearing', 'beer', 'can', 'ears', 'rope', 'net', 'red', 'climbs', 'bridge', 'onto', 'ropes', 'playground', 'running', 'grassy', 'garden', 'surrounded', 'fence', 'throu

In [57]:
ixtoword = {}
wordtoix = {}

ix = 1
for w in vocab:
  wordtoix[w] = ix
  ixtoword[ix] = w
  ix += 1

# Tính toán bảng từ vựng
vocab_size = len(ixtoword) + 1 # Thêm 1 cho từ dùng để padding
print(vocab_size)

1652


In [60]:
def to_lines(descriptions):
  all_desc = list()
  for key in descriptions.keys():
    [all_desc.append(d) for d in descriptions[key]]
  return all_desc #-> chua tat ca cac cau
def max_length(descriptions):
  lines = to_lines(descriptions)
  return max(len(d.split()) for d in lines)
max_length = max_length(train_descriptions)
print(max_length)

34


In [67]:
############################ IV. PHẦN XỬ LÝ ẢNH ĐẦU VÀO ĐỂ ĐƯA VAO MODEL CHÍNH  ############################

def preprocess(image_path):
    print(image_path)
    # Resize ảnh về 299x299 làm đầu vào model
    img = image.load_img(image_path, target_size=(299, 299))
    x = image.img_to_array(img)
    # Thêm một chiều  nữa
    x = np.expand_dims(x, axis=0)
    x = preprocess_input(x)
    print(x.shape)
    return x


In [63]:
#Khỏi tạo model InceptionV3 để trích đặc trưng của ảnh
model = InceptionV3(weights='imagenet')
model_new = Model(model.input, model.layers[-2].output)


96124928/96112376 [==============================] - 2s 0us/step


In [64]:
def encode(image):
  image = preprocess(image)
  fea_vec = model_new.predict(image)
  print(fea_vec.shape)
  fea_vec = np.reashape(fea_vec, fea_vec.shape[1])
  return fea_vec


In [68]:
path = '/content/'
encoding_train = {}
for img in train_img:
  print(img)
  encoding_train[img[len(path_to_image_folder):]] = encode(path + img)
  print(encoding_train[img[len(path_to_image_folder):]])
print(encoding_train)

# Lưu image embedding train lại
with open("encoded_train_images.pkl", "wb") as encoded_pickle:
    dump(encoding_train, encoded_pickle)

encoding_test = {}
for img in test_img:
    encoding_test[img[len(images):]] = encode(img)
with open("encoded_test_images.pkl", "wb") as encoded_pickle:
    dump(encoding_test, encoded_pickle)


Flickr8k/Flicker8k_Dataset/318070878_92ead85868.jpg
/content/Flickr8k/Flicker8k_Dataset/318070878_92ead85868.jpg


AttributeError: ignored

In [ ]:
train_features = load(open('encoded_train_images.pkl', "rb"))
print(train_features)


In [ ]:
############################ V. PHẦN XỬ LÝ MÔ TẢ ĐẦU VÀO ĐỂ ĐƯA VAO MODEL CHÍNH  ############################

glove_dir = ''
embedding_index = {}
f = open(os.path.join(glove_dir, 'glove.6B.200d.txt'), encoding='utf-8')
print(f)
for line in f:
  values = line.split()
  print(values)
  word = values[0]
  print(word)
  coefs = np.asarray(value[1:], dtype='float32')
  embedding_index[word] = coefs
  print(embedding_index[word])
f.close()
embedding_dim = 200
# Tạo ma trận embeding cho bảng từ vững, mỗi từ embeding bằng 1 vector 200
embedding_matrix = np.zeros((vocab_size, embedding_dim))

In [ ]:
for word, i in wordtoix.items():
   # Lấy embeding của Glove gán vào embeding vector
  embedding_vector = embedding_index.get(word)
  print(embeeding_vector)
  if embedding_vector is not None:
    embedding_matrix[i] = embedding_vector
    

In [ ]:
############################ VI. TẠO MODEL CHÍNH VÀ TIẾN HÀNH TRAIN  ############################

# Nhánh 1. Input image vector
inputs_image = Input(shape=(2048,))
dr_1 = Dropout(0.5)(inputs_image)
fc_1 = Dense(256, activation='relu')(drop_1)

# Nhánh 2. Input câu mô tả
inputs_desc = Input(shape=(max_length,))
emb_1 = Embedding(vocab_size, embedding_dim, mask_zero=True)(inputs_desc)
dr_2 = Dropout(0.5)(emb_1)
lstm_1 = LSTM(256)(dr_2)

# Gộp 2 input
decoder_1 = add([fc_1, lstm_1])
fc_3 = Dense(256, activation='relu')(decoder_1)

# Layer output
outputs = Dense(vocab_size, activation='softmax')(fc_3)
model = Model(inputs=[inputs_image, inputs_desc], outputs=outputs)

# Layer 2 dùng GLOVE Model nên set weight thẳng và không cần train
model.layers[2].set_weights([embedding_matrix])
model.layers[2].trainable = False

# Compile model
model.compile(loss='categorical_crossentropy', optimizer='adam')


In [ ]:
def data_generator(descriptions, photos, wordtoix, max_length, num_photos_per_batch):
  X1, X2, y = list(), list(), list()
  n = 0
  while 1:
    for key, desc_list in descriptions.items():
      n += 1;
      photo = photos[key + '.jpg']
      print(photo)
      for desc in desc_list:
        seq = [wordtoix[word] for word in desc.split(' ') if word in wordtoix]
        print(seq)
        for i in range(1, len(seq)):
          in_seq, out_seq = seq[:i], seq[i]
          print(in_seq)
          # pad input sequence
          in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
          print(pad_sequences([in_seq], maxlen=max_length))
          print(in_seq)
          # encode output sequence
          out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
          print(out_seq)
          X1.append(photo)
          X2.append(in_seq)
          y.append(out_seq)
      if n==num_photos_per_batch:
        yield [[array(X1), array(X2)], array(y)]
        X1, X2, y = list(), list(), list()
        n=0

In [ ]:
# Cài đặt tham số train và TRAIN!!!
model.optimizer.lr = 0.0001
epochs = 10 # Số epoch
number_pics_per_batch = 6 # Số lượng ảnh mỗi batch
steps = len(train_descriptions)//number_pics_per_batch # Số bước mỗi epoch

for i in range(epochs):
    generator = data_generator(train_descriptions, train_features, wordtoix, max_length, number_pics_per_bath)
    model.fit_generator(generator, epochs=1, steps_per_epoch=steps, verbose=1)

model.save_weights('model_30.h5')

In [ ]:
############################ VII. KIỂM THỬ XEM MODEL HOẠT ĐỘNG NHƯ NÀO  ############################

# Nạp list các feature của ảnh test (đã encode bằng Inception ở bước trên
with open("encoded_test_images.pkl", "rb") as encoded_pickle:
    encoding_test = load(encoded_pickle)

# Hàm đặt Caption
# Với môi ảnh mới khi test, ta sẽ bắt đầu chuỗi với 'startseq' rồi sau đó cho vào model để dự đoán từ tiếp theo. Ta thêm từ
# vừa được dự đoán vào chuỗi và tiếp tục cho đến khi gặp 'endseq' là kết thúc hoặc cho đến khi chuỗi dài 34 từ.
def setCaption(photo):
    in_text = 'startseq'
    for i in range(max_length):
        sequence = [wordtoix[w] for w in in_text.split() if w in wordtoix]
        sequence = pad_sequences([sequence], maxlen=max_length)
        yhat = model.predict([photo,sequence], verbose=0)
        yhat = np.argmax(yhat)
        word = ixtoword[yhat]
        in_text += ' ' + word
        if word == 'endseq':
            break
    final = in_text.split()
    final = final[1:-1]
    final = ' '.join(final)
    return final

# Dự đoán thử 1 ảnh
image_test_id =5 # Chọn thử anh số 5

# Lấy tên của ảnh só 5 đó
image_name = list(encoding_test.keys())[image_test_id]

# Convert thành vector 2048
image_vector = encoding_test[pic].reshape((1,2048))

# Vẽ ảnh lên màn hình
x=plt.imread(path_to_image_folder + image_name)
plt.imshow(x)
plt.show()

# In kết quả mô tả do model tự đặt cho ảnh
print(setCaption(image))